In [1]:
import numpy as np
from astropy import units as u
from astropy import time
from math import pi

from poliastro.twobody.propagation import propagate
from poliastro.twobody.propagation import cowell
from poliastro.twobody import Orbit
from poliastro.bodies import Earth
from poliastro.plotting import OrbitPlotter3D

from perylune import geom, orbit_tools, perturbers

# Needed to handle TLE into Poliastro's Orbit
from tletools import TLE

In [2]:
import plotly.io as pio
pio.renderers.default = "notebook_connected"

In [3]:
# Let's get the initial PW-Sat2 orbit. Its norad id is 43814
# PW-SAT2 TLE data from 2020-03-15, as published by Celestrak
tle_text = """PW-SAT2                 
1 43814U 18099BJ  20049.76768004  .00014282  00000-0  95610-3 0  9991
2 43814  97.7801 128.6236 0010365 203.2339 156.8317 15.06987254 65660"""
tle_lines = tle_text.strip().splitlines()
tle_pwsat2 = TLE.from_lines(*tle_lines)
orb1 = tle_pwsat2.to_orbit()

# Rotate the orbit plane by 60 degrees, so it's more "edge on" towards the Sun
orb2 = Orbit.from_classical(Earth, orb1.a, orb1.ecc, orb1.inc, orb1.raan + 60*u.deg, orb1.argp, orb1.nu, orb1.epoch)
orbit_tools.print_orb(orb2)

6916 x 6931 km x 97.8 deg (GCRS) orbit around Earth (♁) at epoch 2020-02-18T18:25:27.555456000 (UTC)
a(𝑎)=6923.5493km, b=6923.5456km, e=0.00, i=97.78deg raan(Ω)=188.62deg argp(𝜔)=203.23deg nu(𝜈)=156.88deg
period=5733.29s perapis=6916.3730km(538.24km) apoapsis=6930.7256km(552.59km)


In [4]:
# RECORDER. Records samples.

# These are small utility functions to draw lots of points.
draw_x = []
draw_y = []
draw_z = []
draw_c = [] # color
draw_t = [] # text

decimation_ratio = 3 # Specifies if a given point should be recorded or not.

cnt = 0

def clear_samples():
    global draw_x, draw_y, draw_z, draw_c, draw_t
    draw_x, draw_y, draw_z, draw_c, draw_t = [], [], [], [], []

def record_point(coords, text, color):
    global cnt
    cnt = cnt + 1
    if cnt < decimation_ratio: # Should we remember this point or not
        return
    
    cnt = 0
    x, y, z = coords
    draw_x.append(x)
    draw_y.append(y)
    draw_z.append(z)
    draw_c.append(color)
    draw_t.append(text)

def draw_points(frame, name):
    trace = Scatter3d(x=draw_x, y=draw_y, z=draw_z, name=name, mode="markers", text=draw_t, marker=dict(size=2, color=draw_c))
    frame._figure.add_trace(trace)

In [5]:
# Calculate propagation for the 10 orbits and sample 1000 points along the way
# times is a 1000 points spread out linearly over a time of 10 orbital periods.
# Interesting values for constant acceleration: 2e-5 - spiral, 2e-4 - fast escape trajectory
area = 40 # in m^2
mass = 2.5 # in kg
min_angle = 150 # minimum angle between solar radiation and spacecraft vector. (values 0-90 will slow down the s/c)
orbits = 100

# Record specified number of orbits, with 50 points recorded per orbit
times = np.linspace(0, orbits * orb1.period, 50*orbits)
positions = propagate(orb2, time.TimeDelta(times), method=cowell, rtol=1e-11, ad=perturbers.solar_sail(area, mass, min_angle, None, record_point) )

Force generated by 40.000000 m2 solar sail on 2.500000kg spacecraft generates force 0.000180N, accel of 7.200000e-08 m/s


In [6]:
# Now generate a nice 3D plot of the trajectory.
from plotly.graph_objects import Figure, Layout, Scatter, Scatter3d

frame = OrbitPlotter3D()
frame.set_attractor(Earth)

# Let's pretend this is the Sun
frame._draw_sphere(600*u.km, "red", "Sun", center=[14700, 0, 0] * u.km)

#frame.plot(orb2, color="yellow", label="Initial orbit")
#frame.plot_trajectory(positions, color="green", label="PW-Sat2 (modified)")

draw_points(frame, "points")

frame._layout.width = 1200
frame._layout.height = 800
frame._layout.margin=dict(l=10, r=10, b=10, t=10, pad=4 )
frame.show()

In [7]:
import plotly.express as px
diag1 = px.line(x=times.value, y=positions.norm() - Earth.R, labels={'x': 'time [s]', 'y': 'altitude [km]'})
diag1.update_layout(yaxis=dict(range=[530, 575]))

In [8]:
def moving_avg2(a, n):
    ret = np.cumsum(a, dtype=float)
    ret[n:] = ret[n:] - ret[:-n]
    return ret[n - 1:] / n

window_size = 49
positions_avg = moving_avg2(positions.norm(), window_size)
diag2 = px.line(x=times[window_size-1:].value/86400, y=positions_avg - Earth.R, labels={'x': 'time [days]', 'y': 'altitude [km]'})
diag2.update_layout(yaxis=dict(range=[545, 547]))
diag2.show()

In [9]:
d_time = [0]
d_a = [orb2.a.value]
d_e = [orb2.ecc.value]
d_apo = [orb2.r_a.value]
d_per = [orb2.r_p.value]

for d in range(30):
    tof = (24.0 * u.h).to(u.s) # 24h
    orb2 = orb2.propagate(tof, method=cowell, ad=perturbers.solar_sail(area, mass, min_angle, None, None), rtol=1e-11)
    d_time.append(d_time[-1] + 1)
    d_a.append(orb2.a.value)
    d_e.append(orb2.ecc.value)
    d_apo.append(orb2.r_a.value)
    d_per.append(orb2.r_p.value)

Force generated by 40.000000 m2 solar sail on 2.500000kg spacecraft generates force 0.000180N, accel of 7.200000e-08 m/s
Force generated by 40.000000 m2 solar sail on 2.500000kg spacecraft generates force 0.000180N, accel of 7.200000e-08 m/s
Force generated by 40.000000 m2 solar sail on 2.500000kg spacecraft generates force 0.000180N, accel of 7.200000e-08 m/s
Force generated by 40.000000 m2 solar sail on 2.500000kg spacecraft generates force 0.000180N, accel of 7.200000e-08 m/s
Force generated by 40.000000 m2 solar sail on 2.500000kg spacecraft generates force 0.000180N, accel of 7.200000e-08 m/s
Force generated by 40.000000 m2 solar sail on 2.500000kg spacecraft generates force 0.000180N, accel of 7.200000e-08 m/s
Force generated by 40.000000 m2 solar sail on 2.500000kg spacecraft generates force 0.000180N, accel of 7.200000e-08 m/s
Force generated by 40.000000 m2 solar sail on 2.500000kg spacecraft generates force 0.000180N, accel of 7.200000e-08 m/s
Force generated by 40.000000 m2 

In [10]:
import plotly.graph_objs as go
fig = go.Figure()

r = Earth.R.to(u.km).value

fig.add_trace(go.Line(x = d_time, y = d_a - r, mode="markers", name="semi-major axis"))
fig.add_trace(go.Scatter(x = d_time, y = d_apo - r, mode="markers", name="Apoapsis"))
fig.add_trace(go.Scatter(x = d_time, y = d_per - r, mode="markers", name="Periapsis"))


#fig.add_trace(go.Scatter(x = d_time, y = d_e, mode="markers", name="eccentricity"))


#fig.add_trace(go.Scatter(x = nu_tbl, y = r_tbl, mode="markers", name="distance [km]"))

# Update legend to show at the top
fig.update_layout(legend=dict(orientation="h", yanchor="bottom", y=1.02, xanchor="right", x=1), 
                  xaxis_title="Time [days]", yaxis_title="Altitude [km]", title="Perturbations",
                  margin=dict(l=20, r=20, t=20, b=20))

#fig.update_layout(yaxis=dict(range=[530, 560]))

#fig.add_annotation(x=0, y=7.24, text="periapsis")
#fig.add_annotation(x=pi, y=7.24, text="apoapsis")

fig.show()

/home/thomson/devel/perylune/venv/lib/python3.8/site-packages/plotly/graph_objs/_deprecations.py:378: DeprecationWarning:

plotly.graph_objs.Line is deprecated.
Please replace it with one of the following more specific types
  - plotly.graph_objs.scatter.Line
  - plotly.graph_objs.layout.shape.Line
  - etc.


